# Replication Noteboook

A regression-based approach to the CO$_2$ airborne fraction

[J. Eduardo Vera-Valdés](https://everval.github.io)
[](https://orcid.org/0000-0002-0337-8055)
(Aalborg University)

> **Note**
>
> The following is a replication notebook of the paper by Bennedsen,
> Hillebrand, and Koopman (2024). The replication is done in Julia using
> Quarto as part of the paper *“On measurements errors in CO$_2$
> airborne fraction estimates”* by *J. Eduardo Vera-Valdés* and
> *Charisios Grivas*. This notebook contains no new results.

## Notebook setup

This notebook is written in Julia and uses the following packages:

-   `DataFrames` for data manipulation
-   `XLSX` for reading data from an Excel file
-   `Plots`
-   `LinearAlgebra`
-   `Statsistics`
-   `HypothesisTests`

All packages are available in the Julia registry and can be installed
using the Julia package manager with the following command:

``` julia
using Pkg
Pkg.add("DataFrames", "XLSX", "Plots", "LinearAlgebra", "Statistics", "HypothesisTests")
```

In the following, we load a project environment that contains the
necessary packages. This step is not required if the packages are
already installed in the current environment.

# Airborne fraction

The airborne fraction is the fraction of CO$_2$ emissions that remain in
the atmosphere. It is a key parameter in the carbon cycle and is used to
estimate the impact of human activities on the climate system. The
airborne fraction is defined as the ratio of the increase in atmospheric
CO$_2$ concentration to the total CO$_2$ emissions. It is usually
expressed as a percentage.

## Data

We load the data from an Excel file and plot the CO$_2$ emissions and
the atmospheric CO$_2$ concentration over time.

The data is neatly collected in an Excel file in the author’s GitHub
repository at the following
[link](https://github.com/mbennedsen/New-Approach-to-CO2-Airborne-Fraction/blob/6f3ef9d7dc45a1a65a90b59977629d0c602f807e/AF_data.xlsx).

To ease things up, we have downloaded the data directly from the
repository and saved it in the file `AF_data.xlsx` in the local folder.

We can read the data using the `XLSX.jl` package, convert it to a data
frame using `DataFrames.jl`. We then recover the year, emissions, and
coverage variables. Note that emissions are defined as the sum of fossil
fuels (FF) and land-use and land-coverage changes (LULCC).

In [2]:
using DataFrames, XLSX, LinearAlgebra

path = "AF_data.xlsx"

data = DataFrame(XLSX.readtable(path, "Data"))

year = data[!, 1];
fossilfuels = Vector{Float64}(data[!, 4]);
lulcc = Vector{Float64}(data[!, 6]);
emissions = fossilfuels .+ lulcc;
coverage = Vector{Float64}(data[!, 5]);

VAI = Vector{Float64}(data[!,9]);
ENSO = Vector{Float64}(data[!, 10]);
E = emissions;
G = coverage;

Note that atmospheric concentration growth, denoted `G` from
hereinafter, is transformed into a vector of `Float64` at definition to
avoid type issues. Emissions, the sum of fossil fuels (`fossilfuels`)
and land-use and land-coverage changes (`lulcc`), are denoted by `E`.

Once loaded, we can plot the data using the `Plots.jl` package.

<?xml version="1.0" encoding="utf-8"?>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
<path clip-path="url(#clip180)" d="M248.931 1438.16 L248.931 1435.4 Q259.566 1435.4 265.056 1429.73 Q266.57 1429.73 266.829 1430.08 Q267.088 1430.42 267.088 1432.02 L267.088 1481.7 Q267.088 1484.33 268.385 1485.15 Q269.682 1485.98 275.345 1485.98 L278.155 1485.98 L278.155 1488.7 Q275.043 1488.44 263.803 1488.44 Q252.563 1488.44 249.493 1488.7 L249.493 1485.98 L252.303 1485.98 Q257.88 1485.98 259.22 1485.2 Q260.56 1484.38 260.56 1481.7 L260.56 1435.83 Q255.935 1438.16 248.931 1438.16 Z" fill="#4c4c4c" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip180)" d="M289.05 1449.66 Q289.05 1444.95 290.433 1441.75 Q291.816 1438.51 294.713 1435.31 Q300.03 1429.73 307.725 1429.73 Q311.011 1429.73 313.907 1431.12 Q316.847 1432.5 319.614 1435.66 Q322.424 1438.77 324.11 1444.95 Q325.796 1451.09 325.796 1459.56 Q325.796 1473.27 319.138 1481.96 Q312.524 1490.65 303.575 1490.65 Q297.912 1490.65 294.583 1488.09 Q291.254 1485.5 291.254 1481.09 Q291.254 1478.8 292.551 1477.85 Q293.848 1476.85 295.318 1476.85 Q296.918 1476.85 298.171 1477.94 Q299.425 1478.97 299.425 1480.92 Q299.425 1482.52 298.387 1483.77 Q297.393 1484.98 294.799 1484.98 Q297.35 1488.18 303.489 1488.18 Q305.693 1488.18 307.898 1487.19 Q310.103 1486.15 312.481 1483.69 Q314.902 1481.18 316.371 1475.95 Q317.841 1470.72 317.841 1463.37 L317.841 1460.56 Q314.296 1469.42 306.774 1469.42 Q299.339 1469.42 294.194 1463.71 Q289.05 1458.01 289.05 1449.66 M297.004 1449.75 Q297.004 1458.52 298.604 1461.77 Q301.327 1467.34 306.861 1467.34 Q312.265 1467.34 314.945 1462.55 Q317.668 1457.7 317.668 1451.43 Q317.668 1442.75 316.242 1438.94 Q313.605 1431.94 307.725 1431.94 Q301.889 1431.94 298.863 1437.51 Q297.004 1440.8 297.004 1449.75 Z" fill="#4c4c4c" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip180)" d="M333.318 1460.73 Q333.318 1446.81 340.408 1438.29 Q347.498 1429.73 356.619 1429.73 Q361.937 1429.73 364.877 1432.46 Q367.859 1435.14 367.859 1439.29 Q367.859 1441.58 366.519 1442.57 Q365.179 1443.57 363.796 1443.57 Q362.196 1443.57 360.943 1442.49 Q359.689 1441.41 359.689 1439.46 Q359.689 1435.48 364.574 1435.48 Q362.283 1431.94 356.792 1431.94 Q355.106 1431.94 353.377 1432.46 Q351.648 1432.93 349.4 1434.57 Q347.152 1436.22 345.423 1438.81 Q343.693 1441.41 342.483 1446.29 Q341.272 1451.18 341.272 1457.53 L341.272 1459.65 Q344.904 1450.87 352.34 1450.92 Q359.775 1450.92 364.92 1456.58 Q370.064 1462.24 370.064 1470.63 Q370.064 1479.23 364.704 1484.94 Q359.343 1490.65 351.821 1490.65 Q348.449 1490.65 345.379 1489.22 Q342.353 1487.84 339.5 1484.64 Q336.69 1481.44 335.004 1475.3 Q333.318 1469.16 333.318 1460.73 M341.445 1468.68 Q341.445 1477.37 343.045 1481.52 Q343.304 1482.22 343.866 1483.17 Q344.472 1484.12 345.466 1485.37 Q346.503 1486.58 348.189 1487.4 Q349.875 1488.18 351.821 1488.18 Q357.743 1488.18 360.597 1482.43 Q362.11 1479.23 362.11 1470.54 Q362.11 1461.68 360.51 1458.44 Q357.787 1452.95 352.253 1452.95 Q348.535 1452.95 345.941 1455.5 Q343.391 1458.05 342.396 1461.46 Q341.445 1464.88 341.445 1468.68 Z" fill="#4c4c4c" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip180)" d="M377.327 1460.38 Q377.327 1447.37 380.613 1440.28 Q385.195 1429.73 396.003 1429.73 Q398.294 1429.73 400.672 1430.38 Q403.093 1430.99 406.119 1433.36 Q409.188 1435.74 411.047 1439.63 Q414.592 1447.15 414.592 1460.38 Q414.592 1473.31 411.307 1480.36 Q406.508 1490.65 395.916 1490.65 Q391.939 1490.65 387.875 1488.61 Q383.855 1486.58 381.304 1481.7 Q377.327 1474.39 377.327 1460.38 M384.676 1459.3 Q384.676 1472.66 385.627 1477.98 Q386.708 1483.73 389.648 1486.24 Q392.631 1488.7 395.916 1488.7 Q399.461 1488.7 402.401 1486.06 Q405.384 1483.38 406.292 1477.63 Q407.286 1471.97 407.243 1459.3 Q407.243 1446.98 406.378 1442.05 Q405.211 1436.3 402.098 1434.01 Q399.029 1431.68 395.916 1431.68 Q394.749 1431.68 393.495 1432.02 Q392.285 143

## Classic estimation

Commonly, the airborne fraction is estimated using the following
formula:

$$\frac{G_t}{E_t} =  \alpha + \epsilon_t$$

where $G_t$ is the atmospheric CO$_2$ concentration at time $t$, $E_t$
is the total CO$_2$ emissions at time $t$, and $\epsilon_t$ is the error
term that captures the natural variability in the carbon cycle. The
parameter $\alpha$ is the airborne fraction.

In practice, we estimate $\alpha$ by taking the mean of the ratio of the
coverage to the emissions.

In [4]:
using Statistics

α₁ = mean(G ./ E)

0.43856861803874964

This value is the estimated airborne fraction, which is the consensus
value in the literature.

We plot the yearly airborne fraction and the estimated mean airborne
fraction.

<?xml version="1.0" encoding="utf-8"?>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
<path clip-path="url(#clip270)" d="M278.793 1438.16 L278.793 1435.4 Q289.428 1435.4 294.918 1429.73 Q296.431 1429.73 296.691 1430.08 Q296.95 1430.42 296.95 1432.02 L296.95 1481.7 Q296.95 1484.33 298.247 1485.15 Q299.544 1485.98 305.207 1485.98 L308.017 1485.98 L308.017 1488.7 Q304.905 1488.44 293.665 1488.44 Q282.425 1488.44 279.355 1488.7 L279.355 1485.98 L282.165 1485.98 Q287.742 1485.98 289.082 1485.2 Q290.422 1484.38 290.422 1481.7 L290.422 1435.83 Q285.797 1438.16 278.793 1438.16 Z" fill="#4c4c4c" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip270)" d="M318.912 1449.66 Q318.912 1444.95 320.295 1441.75 Q321.678 1438.51 324.575 1435.31 Q329.892 1429.73 337.587 1429.73 Q340.873 1429.73 343.769 1431.12 Q346.709 1432.5 349.476 1435.66 Q352.286 1438.77 353.972 1444.95 Q355.658 1451.09 355.658 1459.56 Q355.658 1473.27 349 1481.96 Q342.386 1490.65 333.437 1490.65 Q327.774 1490.65 324.445 1488.09 Q321.116 1485.5 321.116 1481.09 Q321.116 1478.8 322.413 1477.85 Q323.71 1476.85 325.18 1476.85 Q326.78 1476.85 328.033 1477.94 Q329.287 1478.97 329.287 1480.92 Q329.287 1482.52 328.249 1483.77 Q327.255 1484.98 324.661 1484.98 Q327.212 1488.18 333.351 1488.18 Q335.555 1488.18 337.76 1487.19 Q339.965 1486.15 342.343 1483.69 Q344.764 1481.18 346.233 1475.95 Q347.703 1470.72 347.703 1463.37 L347.703 1460.56 Q344.158 1469.42 336.636 1469.42 Q329.2 1469.42 324.056 1463.71 Q318.912 1458.01 318.912 1449.66 M326.866 1449.75 Q326.866 1458.52 328.466 1461.77 Q331.189 1467.34 336.723 1467.34 Q342.126 1467.34 344.807 1462.55 Q347.53 1457.7 347.53 1451.43 Q347.53 1442.75 346.104 1438.94 Q343.467 1431.94 337.587 1431.94 Q331.751 1431.94 328.725 1437.51 Q326.866 1440.8 326.866 1449.75 Z" fill="#4c4c4c" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip270)" d="M363.18 1460.73 Q363.18 1446.81 370.27 1438.29 Q377.36 1429.73 386.481 1429.73 Q391.799 1429.73 394.738 1432.46 Q397.721 1435.14 397.721 1439.29 Q397.721 1441.58 396.381 1442.57 Q395.041 1443.57 393.658 1443.57 Q392.058 1443.57 390.804 1442.49 Q389.551 1441.41 389.551 1439.46 Q389.551 1435.48 394.436 1435.48 Q392.145 1431.94 386.654 1431.94 Q384.968 1431.94 383.239 1432.46 Q381.51 1432.93 379.262 1434.57 Q377.014 1436.22 375.285 1438.81 Q373.555 1441.41 372.345 1446.29 Q371.134 1451.18 371.134 1457.53 L371.134 1459.65 Q374.766 1450.87 382.202 1450.92 Q389.637 1450.92 394.782 1456.58 Q399.926 1462.24 399.926 1470.63 Q399.926 1479.23 394.566 1484.94 Q389.205 1490.65 381.683 1490.65 Q378.311 1490.65 375.241 1489.22 Q372.215 1487.84 369.362 1484.64 Q366.552 1481.44 364.866 1475.3 Q363.18 1469.16 363.18 1460.73 M371.307 1468.68 Q371.307 1477.37 372.907 1481.52 Q373.166 1482.22 373.728 1483.17 Q374.333 1484.12 375.328 1485.37 Q376.365 1486.58 378.051 1487.4 Q379.737 1488.18 381.683 1488.18 Q387.605 1488.18 390.459 1482.43 Q391.972 1479.23 391.972 1470.54 Q391.972 1461.68 390.372 1458.44 Q387.649 1452.95 382.115 1452.95 Q378.397 1452.95 375.803 1455.5 Q373.253 1458.05 372.258 1461.46 Q371.307 1464.88 371.307 1468.68 Z" fill="#4c4c4c" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip270)" d="M407.189 1460.38 Q407.189 1447.37 410.475 1440.28 Q415.057 1429.73 425.865 1429.73 Q428.156 1429.73 430.534 1430.38 Q432.955 1430.99 435.981 1433.36 Q439.05 1435.74 440.909 1439.63 Q444.454 1447.15 444.454 1460.38 Q444.454 1473.31 441.168 1480.36 Q436.37 1490.65 425.778 1490.65 Q421.801 1490.65 417.737 1488.61 Q413.717 1486.58 411.166 1481.7 Q407.189 1474.39 407.189 1460.38 M414.538 1459.3 Q414.538 1472.66 415.489 1477.98 Q416.57 1483.73 419.51 1486.24 Q422.493 1488.7 425.778 1488.7 Q429.323 1488.7 432.263 1486.06 Q435.246 1483.38 436.154 1477.63 Q437.148 1471.97 437.105 1459.3 Q437.105 1446.98 436.24 1442.05 Q435.073 1436.3 431.96 1434.01 Q428.891 1431.68 425.778 1431.68 Q424.611 1431.68 423.357 1432.02 Q422.147 1432.37

## A new approach

Recently, Bennedsen, Hillebrand, and Koopman (2024) has suggested a new
approach to estimate the airborne fraction. They propose to use the
following formula:

$$G_t =  \alpha E_t + \epsilon_t,$$

and estimate $\alpha$, the airborne fraction, using ordinary least
squares (OLS). They argue that this approach provides better statistical
properties. Among them, the OLS estimator is super-consistent, meaning
that it converges to the true value at a faster rate than the standard
OLS estimator. They also show that the estimator has lower variance and
is asymptotically normal.

The new approach relies on estimating the **cointegration relationship**
between the emissions and the coverage using OLS. As for all
cointegration analyses, as a first step, we need to check if the
variables are integrated of the same order. We can do this by testing
for the presence of a unit root in the series.

### Unit root test

We use the Augmented Dickey-Fuller (ADF) (Dickey and Fuller 1979) test
to test for the presence of a unit root in the series. The null
hypothesis is that the series has a unit root, while the alternative
hypothesis is that the series is stationary.

In Julia, we can use the `ADFTest` function from the
`HypothesisTests.jl` package to perform the test.

As a demonstration, we test the emissions series for the presence of a
unit root in a model with a trend and two lags.

In [6]:
using HypothesisTests

τᵉₜ = ADFTest(E, :trend, 2)

Augmented Dickey-Fuller unit root test
--------------------------------------
Population details:
    parameter of interest:   coefficient on lagged non-differenced variable
    value under h_0:         0
    point estimate:          -0.262114

Test summary:
    outcome with 95% confidence: fail to reject h_0
    p-value:                     0.2907

Details:
    sample size in regression:          61
    number of lags:                     2
    ADF statistic:                      -2.57687
    Critical values at 1%, 5%, and 10%: [-4.10768 -3.48147 -3.16849]

In this case, the null hypothesis of a unit root in the emissions series
is not rejected.

We can perform the same test for the coverage series while considering
different combinations of models and lags.

In [7]:
# Dataframe to store the results
resultsdf = DataFrame("Variable" => String[], "Model" => String[], "L = 0" => Float64[], "L = 1" => Float64[], "L = 2" => Float64[], "L = 3" => Float64[], "L = 4" => Float64[], "L = 5" => Float64[])

for variable in [:E, :G]
    for model in [:none, :constant, :trend]
        fila = zeros(6)
        for lags in 0:5
            τ = ADFTest(eval(variable), model, lags)
            fila[lags+1] = pvalue(τ)
        end
        push!(resultsdf, [titlecase(string(variable)), titlecase(string(model)), fila...])
    end
end

resultsdf

Based on these results, we cannot reject the null hypothesis of a unit
root in the `emissions` series for all models and lags. For the
`coverage` series, the tests reject except for the model with a trend.
This suggests that both series seem stationary.

### Cointegration test

We can test for cointegration between the emissions and the coverage
using the Engle and Granger (1987) test. The null hypothesis is that
there is no cointegration relationship between the series, while the
alternative hypothesis is that there is a cointegration relationship.

To test for cointegration, we first estimate the OLS regression of the
coverage on the emissions. We then test the residuals for a unit root
using the ADF test. Note that the residuals should be stationary if
there is a cointegration relationship between the series.

In [8]:
α₂ = (E'E) \ (E'G)

0.4477918844144535

The estimated airborne fraction is slightly larger than the classical
estimate.

To test if there is a cointegration relationship, and thus that we have
a valid estimate, we must recover the residuals and test them for a unit
root.

In [9]:
res₂ = G - α₂ * E

τᵣ = ADFTest(res₂, :none, 0)

Augmented Dickey-Fuller unit root test
--------------------------------------
Population details:
    parameter of interest:   coefficient on lagged non-differenced variable
    value under h_0:         0
    point estimate:          -0.963507

Test summary:
    outcome with 95% confidence: reject h_0
    p-value:                     <1e-11

Details:
    sample size in regression:          63
    number of lags:                     0
    ADF statistic:                      -7.58332
    Critical values at 1%, 5%, and 10%: [-2.60156 -1.9459 -1.61324]

The test statistic has to be compared against the critical values
generated by MacKinnon (2010). We can reject the null hypothesis of a
unit root in the residuals, which suggests that there is a cointegration
relationship between the emissions and the coverage and the estimate is
valid.

### Standard errors

We compute the standard errors of the estimates of the airborne fraction
using the formula:

$$SD(\hat{\alpha}) = \sqrt{ \hat{\sigma}^2_\epsilon (E'E)^{-1} },$$

where $\hat{\sigma}^2_\epsilon = \sum\hat{\epsilon}^2/N$ is the estimate
of the variance of the error term and $\hat{\epsilon}_t$ are the
residuals from the regression.

In [10]:
rss₂ = sum((G - α₂ * E).^2)
σ²₂ = rss₂ / (length(G) - 1)

sd₍α₂₎ = sqrt( σ²₂ / (E'E) )

0.014241317441433234

## Additional covariates

We consider adding additional covariates to the model. In particular, we
consider adding $ENSO$ (El Niño Southern Oscillation) and $VAI$
(volcanic activity index) as covariates. These variables are known to
affect the carbon cycle and can potentially influence the airborne
fraction.

We estimate the following model:

$$G_t = \alpha E_t + \gamma_1 ENSO_t + \gamma_2 VAI_t + \epsilon_t,$$

where $ENSO_t$ and $VAI_t$ are the El Niño Southern Oscillation and
volcanic activity index at time $t$, respectively.

Note that the authors first detrend the ENSO series before estimating
the model. We can do this by regressing the series on a time trend and
taking the residuals.

In [11]:
T = length(ENSO)
Xₜ = [ones(T) collect(1:T)]
ρ = (Xₜ'Xₜ) \ (Xₜ'ENSO)
ENSOᵨ = ENSO - Xₜ * ρ;

We estimate the extended model using OLS.

In [12]:
Xₑ = [E ENSOᵨ VAI]

αₑ = (Xₑ'Xₑ) \ (Xₑ'G)

3-element Vector{Float64}:
   0.4696645797106208
   1.0024516231210219
 -15.1482109617327

Standard errors are computed with the multivariate version of the
variance formula:

$$Var(\hat{\alpha}) = \hat{\sigma}^2_\epsilon(X'X)^{-1},$$

where $X$ is the matrix of all regressors.

In [13]:
rssₑ = sum((G - Xₑ*αₑ).^2)
σ²ₑ = rssₑ / (length(G) - 3)
var₍αₑ₎ = σ²ₑ *  inv(Xₑ'Xₑ) 
sqrt.(var₍αₑ₎[1,1])

0.01058726080675776

## Recent subsample

Given the variability of the LULCC measurements at the beginning of the
series, we consider a recent subsample of the data. We consider the data
from 1992 and estimate the airborne fraction using the new approach.

Getting subsample data.

In [14]:
E92 = E[year .>= 1992];
G92 = G[year .>= 1992];
VAI92 = VAI[year .>= 1992];
ENSOᵨ92 = ENSOᵨ[year .>= 1992];

Estimating in the subsample.

Simple specification.

In [15]:
α92₂ = (E92'E92) \ (E92'G92)
rss92₂ = sum((G92 - α92₂ * E92).^2)
σ92²₂ = rss92₂ / (length(G92) - 1)
sd₍α92₂₎ = sqrt( σ92²₂ / (E92'E92) )

[α92₂ sd₍α92₂₎]

1×2 Matrix{Float64}:
 0.44967  0.017309

In [16]:
X92ₑ = [E92 ENSOᵨ92 VAI92]
α92ₑ = (X92ₑ'X92ₑ) \ (X92ₑ'G92)

rss92ₑ = sum((G92 - X92ₑ*α92ₑ).^2)
σ92²ₑ = rss92ₑ / (length(G92) - 3)
var₍α92ₑ₎ = σ92²ₑ * inv(X92ₑ'X92ₑ) 

[α92ₑ var₍α92ₑ₎]

3×4 Matrix{Float64}:
   0.461253   0.000126359   9.12279e-5  -0.0092892
   1.02214    9.12279e-5    0.0296269   -0.157186
 -17.5878    -0.0092892    -0.157186    13.5323

## Other datasets

We can also test the new approach on other datasets. We can use the same
methodology to estimate the airborne fraction. The preferred data for
the LULCC emissions are from the Global Carbon Project (Friedlingstein
et al. 2023). However, we can also use data from Houghton and Castanho
(2022) and Marle et al. (2022).

In [17]:
lulcc₂ = Vector{Float64}(data[!, 7]);
lulcc₃ = Vector{Float64}(data[!, 8]);

E₂ = fossilfuels .+ lulcc₂;
E₃ = fossilfuels .+ lulcc₃;

α₆ = (E₂'E₂) \ (E₂'G)
rss₆ = sum((G - α₆ * E₂).^2)
σ²₆ = rss₆ / (length(G) - 1)
sd₍α₆₎ = sqrt( σ²₆ / (E₂'E₂) )

α₇ = (E₃'E₃) \ (E₃'G)
rss₇ = sum((G - α₇ * E₃).^2)
σ²₇ = rss₇ / (length(G) - 1)
sd₍α₇₎ = sqrt( σ²₇ / (E₃'E₃) )

[α₆ sd₍α₆₎; α₇ sd₍α₇₎]

2×2 Matrix{Float64}:
 0.475539  0.0152315
 0.490211  0.0157142

## Deming regression estimator

We can also estimate the airborne fraction using Deming regression
(Deming 1943). Deming regression is a method for estimating the
parameters of a linear regression model when both the dependent and
independent variables are subject to measurement error. The Deming
regression assumes that the measurement errors in the dependent and
independent variables are normally distributed with known variances.

The Deming regression estimator is given by:

$$
\hat{\alpha}_{Deming} = \frac{M_{GG}-\delta M_{EE} + \sqrt{(M_{GG}-\delta M_{EE})^2+4\delta M^2_{EG}}}{2M_{EG}},
$$

where

$$M_{GG} = \frac{1}{T}\sum_{t=1}^T G_t^2,$$
$$M_{EE} = \frac{1}{T}\sum_{t=1}^T E_t^2,$$
$$M_{EG} = \frac{1}{T}\sum_{t=1}^T E_t G_t,$$

and $\delta = \frac{Variance(\omega_{G,t})}{Variance(\eta_{E,t})}$ is
the ratio of the variance of the measurement error in the coverage to
the variance of the measurement error in emissions.

Several values for $\delta$ are tried, given that the true value is
unknown.

In [18]:
M₍ₑₑ₎ = E'E
M₍ₑₐ₎ = E'G
M₍ₐₐ₎ = G'G

δ = zeros(2, 5)
δ[ 1, :] = [0.2 0.5 1 2 5]

for ii = 1:5
    δ[ 2, ii] = ( M₍ₐₐ₎ - δ[1, ii] * M₍ₑₑ₎ + sqrt( (M₍ₐₐ₎ - δ[1, ii] * M₍ₑₑ₎)^2 + 4 * δ[1, ii] * M₍ₑₐ₎^2 ) ) / (2 * M₍ₑₐ₎)
end

display(δ)

2×5 Matrix{Float64}:
 0.2       0.5       1.0     2.0       5.0
 0.462305  0.456067  0.4526  0.450406  0.448895

Other drawbacks of the Deming regression is that there is no closed form
expression to obtain the standard errors. It also cannot easily handle
additional regressors like in the preferred specification. We solve
these issues in the paper: *On measurements errors in CO$_2$ airborne
fraction estimates* by *J. Eduardo Vera-Valdés* and *Charisios Grivas*.

## Summary of results

In [19]:
results_replication = DataFrame("Model" => String[], "Estimate" => Float64[], "Std. Error" => Float64[], "Confidence Int." => Vector{Float64}[] )
nd = 4;

push!(results_replication, ["Regression", α₂, sd₍α₂₎, round.([α₂ - 1.96 * sd₍α₂₎, α₂ + 1.96 * sd₍α₂₎], digits=nd) ] )
push!(results_replication, ["Regression with ENSO and VAI", αₑ[1], sqrt(var₍αₑ₎[1,1]), round.([αₑ[1] - 1.96 * sqrt(var₍αₑ₎[1,1]), αₑ[1] + 1.96 * sqrt(var₍αₑ₎[1,1])], digits=nd) ] )
push!(results_replication, ["Regression from 1992", α92₂, sd₍α92₂₎, round.([α92₂ - 1.96 * sd₍α92₂₎, α92₂ + 1.96 * sd₍α92₂₎], digits=nd) ] )
push!(results_replication, ["Regression from 1992 with ENSO and VAI", α92ₑ[1], sqrt(var₍α92ₑ₎[1,1]), round.([α92ₑ[1] - 1.96 * sqrt(var₍α92ₑ₎[1,1]), α92ₑ[1] + 1.96 * sqrt(var₍α92ₑ₎[1,1])], digits=nd) ] )
push!(results_replication, ["Regression with LULCC (H&N)", α₆, sd₍α₆₎, round.([α₆ - 1.96 * sd₍α₆₎, α₆ + 1.96 * sd₍α₆₎], digits=nd) ] )
push!(results_replication, ["Regression with LULCC (vMa)", α₇, sd₍α₇₎, round.([α₇ - 1.96 * sd₍α₇₎, α₇ + 1.96 * sd₍α₇₎], digits=nd) ] )
push!(results_replication, ["Deming regression (δ=0.2)", δ[2, 1], NaN, [NaN] ] )
push!(results_replication, ["Deming regression (δ=0.5)", δ[2, 2], NaN, [NaN] ] )
push!(results_replication, ["Deming regression (δ=1)", δ[2, 3], NaN, [NaN] ] )
push!(results_replication, ["Deming regression (δ=2)", δ[2, 4], NaN, [NaN] ] )
push!(results_replication, ["Deming regression (δ=5)", δ[2, 5], NaN, [NaN] ] )
results_replication.Estimate = round.(results_replication.Estimate, digits=nd)
results_replication."Std. Error" = round.(results_replication."Std. Error", digits=nd)
display(results_replication)

Note that Bennedsen, Hillebrand, and Koopman (2024) considered
heteroscedasticity and autocorrelation robust standard errors.
Nonetheless, their selected bandwidth is quite small, so that they are
almost identical to the OLS standard errors. We report here the latter
for simplicity.

## References

Bennedsen, Mikkel, Eric Hillebrand, and Siem Jan Koopman. 2024. “A
Regression-Based Approach to the CO2 Airborne Fraction.” *Nature
Communications* 15 (1): 8507.
<https://doi.org/10.1038/s41467-024-52728-1>.

Deming, William Edwards. 1943. *Statistical Adjustment of Data.* wiley.

Dickey, David A, and Wayne A Fuller. 1979. “Distribution of the
Estimators for Autoregressive Time Series with a Unit Root.” *Journal of
the American Statistical Association* 74 (366a): 427–31.

Engle, Robert F., and C. W. J. Granger. 1987. “Co-Integration and Error
Correction: Representation, Estimation, and Testing.” *Econometrica* 55
(2): 251–76. <https://www.jstor.org/stable/1913236>.

Friedlingstein, Pierre, Michael O’sullivan, Matthew W Jones, Robbie M
Andrew, Dorothee CE Bakker, Judith Hauck, Peter Landschützer, et al.
2023. “Global Carbon Budget 2023.” *Earth System Science Data* 15 (12):
5301–69.

Houghton, Richard A, and Andrea Castanho. 2022. “Annual Emissions of
Carbon from Land Use, Land-Use Change, and Forestry 1850–2020.” *Earth
System Science Data Discussions* 2022: 1–36.

MacKinnon, James G. 2010. “Critical Values for Cointegration Tests.”
Queen’s Economics Department Working Paper.

Marle, Margreet JE van, Dave van Wees, Richard A Houghton, Robert D
Field, Jan Verbesselt, and Guido R van der Werf. 2022. “RETRACTED
ARTICLE: New Land-Use-Change Emissions Indicate a Declining CO2 Airborne
Fraction.” *Nature* 603 (7901): 450–54.